# Versuch Konstruktion Zeitachse im Datensatz

- einzigartige ObjektIDs
    - Einzigartigkeit verifizieren mittels HObjektText
- je ObjektID Identifikation von Störungen
- Analyse ähnlicher Störbilder
- Nutzung:
    - VorgangsTypName 
    - VorgangsBeschreibung
    - VorgangsArtText
    - evtl. concat

In [1]:
%load_ext autoreload
%autoreload 2

In [1]:
import numpy as np
import pandas as pd
from pandas import DataFrame, Series
import spacy
from spacy.lang.de import German as GermanSpacyModel
import sentence_transformers
from sentence_transformers import SentenceTransformer
from collections import Counter
from itertools import combinations
from dateutil.parser import parse
import re


import logging
import sys
import pickle
import os
from pathlib import Path

from lang_main import (
    save_pickle,
    load_pickle,
    SAVE_PATH_FOLDER,
)

LOGGING_LEVEL = 'INFO'
logging.basicConfig(level=LOGGING_LEVEL, stream=sys.stdout)
logger = logging.getLogger('base')

A:\Arbeitsaufgaben\lang-main\.venv\Lib\site-packages\transformers\utils\generic.py:441: UserWarning: torch.utils._pytree._register_pytree_node is deprecated. Please use torch.utils._pytree.register_pytree_node instead.
  _torch_pytree._register_pytree_node(


INFO:ihm_analyse.helpers:Loaded TOML config file successfully.


In [2]:
model_stfr = SentenceTransformer('sentence-transformers/all-mpnet-base-v2')

INFO:sentence_transformers.SentenceTransformer:Load pretrained SentenceTransformer: sentence-transformers/all-mpnet-base-v2


A:\Arbeitsaufgaben\lang-main\.venv\Lib\site-packages\huggingface_hub\file_download.py:1132: FutureWarning: `resume_download` is deprecated and will be removed in version 1.0.0. Downloads always resume when possible. If you want to force a new download, use `force_download=True`.
  warnings.warn(
A:\Arbeitsaufgaben\lang-main\.venv\Lib\site-packages\transformers\utils\generic.py:309: UserWarning: torch.utils._pytree._register_pytree_node is deprecated. Please use torch.utils._pytree.register_pytree_node instead.
  _torch_pytree._register_pytree_node(
A:\Arbeitsaufgaben\lang-main\.venv\Lib\site-packages\transformers\utils\generic.py:309: UserWarning: torch.utils._pytree._register_pytree_node is deprecated. Please use torch.utils._pytree.register_pytree_node instead.
  _torch_pytree._register_pytree_node(
A:\Arbeitsaufgaben\lang-main\.venv\Lib\site-packages\huggingface_hub\file_download.py:1132: FutureWarning: `resume_download` is deprecated and will be removed in version 1.0.0. Downloads 

INFO:sentence_transformers.SentenceTransformer:Use pytorch device_name: cpu


In [3]:
p = Path(os.getcwd()) / SAVE_PATH_FOLDER
p

WindowsPath('A:/Arbeitsaufgaben/lang-main/test-notebooks/results/test_new2')

In [4]:
folder = list(p.glob(r'*'))
folder

[WindowsPath('A:/Arbeitsaufgaben/lang-main/test-notebooks/results/test_new2/Pipe-TargetFeature_Step-3_remove_NA.pickle')]

In [5]:
ret = load_pickle(folder[0])
data = ret[0]
len(data)

INFO:ihm_analyse.helpers:Loaded file successfully.


123457

In [6]:
data.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 123457 entries, 0 to 123456
Data columns (total 20 columns):
 #   Column                   Non-Null Count   Dtype         
---  ------                   --------------   -----         
 0   VorgangsID               123457 non-null  int64         
 1   ObjektID                 123457 non-null  int64         
 2   HObjektText              123442 non-null  object        
 3   ObjektArtID              123457 non-null  int64         
 4   ObjektArtText            122880 non-null  object        
 5   VorgangsTypID            123457 non-null  int64         
 6   VorgangsTypName          123457 non-null  object        
 7   VorgangsDatum            123457 non-null  datetime64[ns]
 8   VorgangsStatusId         123457 non-null  int64         
 9   VorgangsPrioritaet       123457 non-null  int64         
 10  VorgangsBeschreibung     123457 non-null  object        
 11  VorgangsOrt              490 non-null     object        
 12  VorgangsArtText 

---

# Gather timeline candidates

In [23]:
from lang_main.analysis.timeline import (
    non_relevant_obj_ids,
    remove_non_relevant_obj_ids,
    filter_activities_per_obj_id,
    generate_model_input,
    get_timeline_candidates_index,
)

In [24]:
ret = load_pickle(folder[0])
data = ret[0]
print(f"{len(data)=}")
data = remove_non_relevant_obj_ids(data, thresh_unique_feat_per_id=4)
data.info()

INFO:ihm_analyse.helpers:Loaded file successfully.
len(data)=123457
<class 'pandas.core.frame.DataFrame'>
Index: 122958 entries, 0 to 123456
Data columns (total 20 columns):
 #   Column                   Non-Null Count   Dtype         
---  ------                   --------------   -----         
 0   VorgangsID               122958 non-null  int64         
 1   ObjektID                 122958 non-null  int64         
 2   HObjektText              122953 non-null  object        
 3   ObjektArtID              122958 non-null  int64         
 4   ObjektArtText            122880 non-null  object        
 5   VorgangsTypID            122958 non-null  int64         
 6   VorgangsTypName          122958 non-null  object        
 7   VorgangsDatum            122958 non-null  datetime64[ns]
 8   VorgangsStatusId         122958 non-null  int64         
 9   VorgangsPrioritaet       122958 non-null  int64         
 10  VorgangsBeschreibung     122958 non-null  object        
 11  VorgangsOrt    

In [25]:
data['VorgangsTypName'].unique()

array(['Reparaturauftrag (Portal)', 'Wartung', 'Störungsmeldung'],
      dtype=object)

In [26]:
activity_types = [
    'Reparaturauftrag (Portal)',
    'Störungsmeldung',
]

(data, num_activities_per_obj_id) =\
filter_activities_per_obj_id(data, relevant_activity_types=activity_types)
num_activities_per_obj_id

ObjektID
1       283
1654    243
7       223
151     189
140     140
       ... 
1698      2
683       2
1135      2
2170      2
297       2
Name: count, Length: 366, dtype: int64

In [27]:
data.info()

<class 'pandas.core.frame.DataFrame'>
Index: 6104 entries, 0 to 123456
Data columns (total 20 columns):
 #   Column                   Non-Null Count  Dtype         
---  ------                   --------------  -----         
 0   VorgangsID               6104 non-null   int64         
 1   ObjektID                 6104 non-null   int64         
 2   HObjektText              6103 non-null   object        
 3   ObjektArtID              6104 non-null   int64         
 4   ObjektArtText            6087 non-null   object        
 5   VorgangsTypID            6104 non-null   int64         
 6   VorgangsTypName          6104 non-null   object        
 7   VorgangsDatum            6104 non-null   datetime64[ns]
 8   VorgangsStatusId         6104 non-null   int64         
 9   VorgangsPrioritaet       6104 non-null   int64         
 10  VorgangsBeschreibung     6104 non-null   object        
 11  VorgangsOrt              0 non-null      object        
 12  VorgangsArtText          6104 non-nul

In [28]:
# VorgangsTypName, VorgangsArtText, VorgangsBeschreibung
prop_interest = ['VorgangsTypName', 'VorgangsArtText', 'VorgangsBeschreibung']
prop_interest = ['VorgangsArtText', 'VorgangsBeschreibung']
prop_interest = ['VorgangsBeschreibung']

target_feature_name = 'nlp_model_input'

In [29]:
anlys_data = generate_model_input(data, target_feature_name, model_input_features=prop_interest)

In [30]:
anlys_data.info()

<class 'pandas.core.frame.DataFrame'>
Index: 6104 entries, 0 to 123456
Data columns (total 21 columns):
 #   Column                   Non-Null Count  Dtype         
---  ------                   --------------  -----         
 0   VorgangsID               6104 non-null   int64         
 1   ObjektID                 6104 non-null   int64         
 2   HObjektText              6103 non-null   object        
 3   ObjektArtID              6104 non-null   int64         
 4   ObjektArtText            6087 non-null   object        
 5   VorgangsTypID            6104 non-null   int64         
 6   VorgangsTypName          6104 non-null   object        
 7   VorgangsDatum            6104 non-null   datetime64[ns]
 8   VorgangsStatusId         6104 non-null   int64         
 9   VorgangsPrioritaet       6104 non-null   int64         
 10  VorgangsBeschreibung     6104 non-null   object        
 11  VorgangsOrt              0 non-null      object        
 12  VorgangsArtText          6104 non-nul

In [31]:
anlys_data.loc[anlys_data['HObjektText'].isna()]

VorgangsID  ObjektID HObjektText  ObjektArtID  \
52136      262888       315         NaN           32   

                                     ObjektArtText  VorgangsTypID  \
52136  Flurförderzeuge / Putzmaschine / Rasenmäher              3   

                 VorgangsTypName VorgangsDatum  VorgangsStatusId  \
52136  Reparaturauftrag (Portal)    2022-07-11                 5   

       VorgangsPrioritaet  ... VorgangsOrt VorgangsArtText ErledigungsDatum  \
52136                   0  ...         NaN  Flurförderzeug       2022-07-12   

         ErledigungsArtText ErledigungsBeschreibung MPMelderArbeitsplatz  \
52136  Intern UTT - Wartung         Räder gereinigt              Versand   

      MPAbteilungBezeichnung Arbeitsbeginn ErstellungsDatum  \
52136                Versand    2022-07-12       2022-07-11   

                   nlp_model_input  
52136  Laufrollen verstopft (Garn)  

[1 rows x 21 columns]

In [32]:
anlys_data.loc[anlys_data['ObjektID']==315]

VorgangsID  ObjektID            HObjektText  ObjektArtID  \
1082        201309       315  B15, Niederhubwagen,            32   
1710         65146       315  B15, Niederhubwagen,            32   
3525        146538       315  B15, Niederhubwagen,            32   
3786        260011       315  B15, Niederhubwagen,            32   
11101       520758       315  B15, Niederhubwagen,            32   
13645       139405       315  B15, Niederhubwagen,            32   
14105        62552       315  B15, Niederhubwagen,            32   
22686        61759       315  B15, Niederhubwagen,            32   
24898        51614       315  B15, Niederhubwagen,            32   
25405        65283       315  B15, Niederhubwagen,            32   
26160        48299       315  B15, Niederhubwagen,            32   
32457        11022       315  B15, Niederhubwagen,            32   
36300       133603       315  B15, Niederhubwagen,            32   
39483       570650       315  B15, Niederhubwagen,            32   
46099        70283       315  B15, Niederhubwagen,            32   
47628       116364       315  B15, Niederhubwagen,            32   
47634       116362       315  B15, Niederhubwagen,            32   
52136       262888       315                    NaN           32   
57067       106178       315  B15, Niederhubwagen,            32   
60040       102674       315  B15, Niederhubwagen,            32   
62125        25451       315  B15, Niederhubwagen,            32   
66746        30355       315  B15, Niederhubwagen,            32   
79821       272506       315  B15, Niederhubwagen,            32   
107351      495093       315  B15, Niederhubwagen,            32   
121822      496095       315  B15, Niederhubwagen,            32   
122399      513437       315  B15, Niederhubwagen,            32   

                                      ObjektArtText  VorgangsTypID  \
1082    Flurförderzeuge / Putzmaschine / Rasenmäher              3   
1710    Flurförderzeuge / Putzmaschine / Rasenmäher              3   
3525    Flurförderzeuge / Putzmaschine / Rasenmäher              3   
3786    Flurförderzeuge / Putzmaschine / Rasenmäher              3   
11101   Flurförderzeuge / Putzmaschine / Rasenmäher              3   
13645   Flurförderzeuge / Putzmaschine / Rasenmäher              2   
14105   Flurförderzeuge / Putzmaschine / Rasenmäher              3   
22686   Flurförderzeuge / Putzmaschine / Rasenmäher              3   
24898   Flurförderzeuge / Putzmaschine / Rasenmäher              3   
25405   Flurförderzeuge / Putzmaschine / Rasenmäher              3   
26160   Flurförderzeuge / Putzmaschine / Rasenmäher              3   
32457   Flurförderzeuge / Putzmaschine / Rasenmäher              3   
36300   Flurförderzeuge / Putzmaschine / Rasenmäher              3   
39483   Flurförderzeuge / Putzmaschine / Rasenmäher              3   
46099   Flurförderzeuge / Putzmaschine / Rasenmäher              3   
47628   Flurförderzeuge / Putzmaschine / Rasenmäher              3   
47634   Flurförderzeuge / Putzmaschine / Rasenmäher              3   
52136   Flurförderzeuge / Putzmaschine / Rasenmäher              3   
57067   Flurförderzeuge / Putzmaschine / Rasenmäher              3   
60040   Flurförderzeuge / Putzmaschine / Rasenmäher              3   
62125   Flurförderzeuge / Putzmaschine / Rasenmäher              3   
66746   Flurförderzeuge / Putzmaschine / Rasenmäher              3   
79821   Flurförderzeuge / Putzmaschine / Rasenmäher              3   
107351  Flurförderzeuge / Putzmaschine / Rasenmäher              3   
121822  Flurförderzeuge / Putzmaschine / Rasenmäher              3   
122399  Flurförderzeuge / Putzmaschine / Rasenmäher              3   

                  VorgangsTypName VorgangsDatum  VorgangsStatusId  \
1082    Reparaturauftrag (Portal)    2022-02-21                 5   
1710    Reparaturauftrag (Portal)    2020-11-12                 5   
3525    Reparaturauftrag (Portal)    2021-12-16                 5   
3786

In [33]:
test = num_activities_per_obj_id.iloc[300:302].copy()
test

ObjektID
640    3
287    3
Name: count, dtype: int64

In [34]:
tl_candidates = get_timeline_candidates_index(
    data=anlys_data,
    num_activities_per_obj_id=test,
    model=model_stfr,
    cos_sim_threshold=0.1,
    model_input_feature=target_feature_name,
)

In [35]:
for (obj_id, cands) in tl_candidates:
    print(f'{obj_id=}, {cands=}')

INFO:ihm_analyse.graphs:Graph properties: 3 Nodes, 3 Edges
INFO:ihm_analyse.graphs:Node memory: 0.09 KB
INFO:ihm_analyse.graphs:Edge memory: 0.16 KB
INFO:ihm_analyse.graphs:Total memory: 0.26 KB
obj_id=640, cands=[14720, 27393, 3878]
INFO:ihm_analyse.graphs:Graph properties: 3 Nodes, 3 Edges
INFO:ihm_analyse.graphs:Node memory: 0.09 KB
INFO:ihm_analyse.graphs:Edge memory: 0.16 KB
INFO:ihm_analyse.graphs:Total memory: 0.26 KB
obj_id=287, cands=[19665, 61717, 15983]


In [36]:
res = anlys_data.loc[[14720, 27393, 3878]]
res

VorgangsID  ObjektID            HObjektText  ObjektArtID  \
14720        3798       640  R35, Schnelllauftor,            36   
27393       10974       640  R35, Schnelllauftor,            36   
3878       145910       640  R35, Schnelllauftor,            36   

                   ObjektArtText  VorgangsTypID            VorgangsTypName  \
14720  Falt- und Schnelllauftore              2            Störungsmeldung   
27393  Falt- und Schnelllauftore              3  Reparaturauftrag (Portal)   
3878   Falt- und Schnelllauftore              2            Störungsmeldung   

      VorgangsDatum  VorgangsStatusId  VorgangsPrioritaet  ... VorgangsOrt  \
14720    2019-07-03                 5                   0  ...         NaN   
27393    2019-09-11                 5                   0  ...         NaN   
3878     2021-11-24                 5                   0  ...         NaN   

                     VorgangsArtText ErledigungsDatum  \
14720                 Schnelllauftor       2019-07-04   
27393                 Schnelllauftor       2019-09-11   
3878   Allgemeine Reparaturarbeiten        2021-12-16   

            ErledigungsArtText  \
14720            Reparatur UTT   
27393            Reparatur UTT   
3878   Intern UTT - Reparatur    

                                 ErledigungsBeschreibung MPMelderArbeitsplatz  \
14720      Elektrokabel aus dem Führungsrahmen entfernt.                  NaN   
27393  vom Schnelllauftor die Schiene ausgebaut und a...              Weberei   
3878   Beim Tor unterstes Torelement ausgerichtet abe...                  NaN   

      MPAbteilungBezeichnung Arbeitsbeginn ErstellungsDatum  \
14720                    NaN    2019-07-04       2019-07-03   
27393                Weberei    2019-09-11       2019-09-11   
3878                     NaN    2021-12-16       2021-11-24   

                                         nlp_model_input  
14720  Behang hängt bei Bedinung schief  \nbitte kont...  
27393  Schnellauftor R35  Defekt in Halle 54\nGewalts...  
3878             Abdeckung austauschen, wurde angefahren  

[3 rows x 21 columns]

In [49]:
import plotly.express as px
import plotly.io as pio
pio.renderers.default = 'iframe'

In [73]:
def filter_df(data, obj_id, cands):
    res = data.loc[cands]
    texts = res['HObjektText']
    obj_text = texts.loc[~(texts.isna())].iat[0]
    obj_text = obj_text.strip(r' ,.:')
    return obj_text

In [74]:
text = filter_df(anlys_data, 640, [14720, 27393, 3878])

In [75]:
text

'R35, Schnelllauftor'

In [50]:
t = res['ErstellungsDatum'].sort_values(ascending=True)

In [51]:
t

14720   2019-07-03
27393   2019-09-11
3878    2021-11-24
Name: ErstellungsDatum, dtype: datetime64[ns]

In [57]:
fig = px.scatter(data_frame=res, x='ErstellungsDatum')
fig.update_yaxes(type='category')

In [113]:
# filter each ObjID, get model input with index
for obj_id in test.index:
    test2 = anlys_data.loc[anlys_data[test.index.name]==obj_id]
    test2 = test2[target_feature_name]
test2

123735    Kettschrauben abgebrochen (Gewinde schneiden)
Name: nlp_model_input, dtype: object

In [292]:
batch = obj_data.conc.to_list()
batch

['Regalbediengerät fällt immer wieder aus.\nFehlercode VZK ER 204/ER 226 während der Fahrt.\nFehlercode VZK ER 208 / ER 209',
 'Hochregalstapler stoppt ständig.\nFehleranzeige: VZA ER 179',
 'Hier wird ein Hochlagerstapler Spezialist benötigt..\n\nToyota Herr Jörg Langner tel_Nr. 0172-8218647 UVV\nDambach B12 (A)\n\n\nFehlermeldung:\nKetten schlaff\nFehlermeldung: VZK - ER229\n\n\nfehlermeldung trift nur sporadisch auf...\nLaut Herr Frick beibt Gerät in Höhe stehen und fährt erst nach mehrmaligem Neustart oder teilweiseerst nach bis zu ca. 30Min.\nwieder. \n\nLaut Herr Spennesberger soll Herr Langner (Toyota) anscheinend nächste Woche auch zur UVV erscheinen.',
 'Gabeldrehen defekt > Kette gerissen\n\nSeitenhub defekt > Führung verbogen gerissen\n\nStapler ist irgendwo (? Regal ? ) angefahren\n\n',
 'Herrn Langner bitte nochmals anfordern. Aktuell steht das Fahrzeug. Fehlercode VZA OK / VZK Error(s) Er229 / VZB OK\nFr. Stöppel hat Herr Langer benachrichtigt.\nElektriker bitte Schalter 

In [293]:
embds = model_stfr.encode(batch)

Batches: 100%|██████████| 1/1 [00:01<00:00,  1.77s/it]


In [294]:
cos_sim = sentence_transformers.util.cos_sim(embds, embds).numpy()
np.fill_diagonal(cos_sim, 0.)
cos_sim = np.triu(cos_sim)
#cos_sim

In [299]:
THRESHOLD = 0.5
#np.where(cos_sim > THRESHOLD, cos_sim, 0)
indices = np.argwhere(cos_sim >= THRESHOLD)

In [287]:
for idx_pair in indices:
    idx1 = idx_pair[0]
    idx2 = idx_pair[1]
    text1 = batch[idx1]
    text2 = batch[idx2]
    
    cos_sim_val = cos_sim[idx1,idx2]
    
    print(f"{text1=}, \n {text2=}, \n {cos_sim_val=} \n\n")

text1='Reparaturauftrag (Portal) - Allgemeine Reparaturarbeiten  - bei Laser1 an Bandsäge band abgerissen\nund bitte Hydraulikbremsfeder kontrollieren', 
 text2='Reparaturauftrag (Portal) - Allgemeine Reparaturarbeiten  - Bandsäge ein-aus schalter defekt.\n(Haltering von Stellschraube gebrochen) dieser fährt auf Endschalter', 
 cos_sim_val=0.60256654 


text1='Reparaturauftrag (Portal) - Allgemeine Reparaturarbeiten  - bei Laser1 an Bandsäge band abgerissen\nund bitte Hydraulikbremsfeder kontrollieren', 
 text2='Reparaturauftrag (Portal) - Allgemeine Reparaturarbeiten  - Bandsäge defekt geht sehr schwer hoch Hydraulik Problem     NICHT ERLEDIGT!!!!!!!\n\n13.06.2022: Feder eingebaut durch Hr. Özdemir und funtkionstüchtig', 
 cos_sim_val=0.56998414 


text1='Reparaturauftrag (Portal) - Allgemeine Reparaturarbeiten  - Bandsäge ein-aus schalter defekt.\n(Haltering von Stellschraube gebrochen) dieser fährt auf Endschalter', 
 text2='Reparaturauftrag (Portal) - Allgemeine Reparaturarbeiten  

In [290]:
# test ID with small amount of entries
# e.g. 19
OBJ_ID_INTEREST = 311 # 311 # 87 #19
obj_data = anlys_data.loc[
    ((anlys_data.ObjektID==OBJ_ID_INTEREST) & 
    (anlys_data.VorgangsTypName=='Reparaturauftrag (Portal)')),:
].copy()

'\nobj_data = anlys_data.loc[\n    anlys_data.ObjektID==OBJ_ID_INTEREST,:\n].copy()\n'

In [3]:
LOAD_CALC_FILES = False

# load preprocessed dataset
DATA_SET_ID = 'Export4'

SAVE_PATH_DF_DUPL_OCCUR = f'./02_1_Preprocess1/{DATA_SET_ID}_00_DF_wo_dupl.parquet'
data = pd.read_parquet(SAVE_PATH_DF_DUPL_OCCUR)

data.head()

In [11]:
data.iloc[:10,:].HObjektText.unique()

array(['427 C , Webmaschine, DL 280 EMS Breite 280 ',
       '621 C , Webmaschine, DL 280 EMS Breite 280 ',
       '285 C, Webmaschine, SG 220 EMS', '107, Webmaschine, OM 220 EOS',
       '00138, Schärmaschine 9, ', 'Warenschau allgemein',
       'Neben der Türe', 'Schlagloch im Kettregalgang',
       '294 C, Webmaschine, SG 240 EMS',
       'Umkleideraum Herren beim Haupteingang'], dtype=object)

In [13]:
ret = data.loc[(data.ObjektID==0), 'HObjektText']

In [14]:
len(ret)

517

In [15]:
len(ret.unique())

306

In [25]:
# mapping: dict[ObjektID, (total num of entries for given ID,
# total num of unique objekt texts)]
id_to_num_objs: dict[int, (int, int)] = dict()

for obj_id in data.ObjektID.unique():
    temp = data.loc[(data.ObjektID==obj_id), 'HObjektText']
    temp1 = len(temp)
    temp2 = len(temp.unique())
    
    id_to_num_objs[obj_id] = (temp1, temp2)
    
    if temp2 > 3:
        print(f"{obj_id=}, uni texts: {temp2}")

obj_id=0, uni texts: 306
obj_id=906, uni texts: 4
obj_id=1110, uni texts: 4


In [199]:
# get ObIDs with repair orders and sort by number of occurences
repair_freq = data.loc[(data.VorgangsTypName=='Reparaturauftrag (Portal)'), 'ObjektID'].value_counts()
repair_freq

ObjektID
0       443
1       253
1654    223
7       207
151     185
       ... 
686       1
942       1
387       1
1122      1
1797      1
Name: count, Length: 389, dtype: int64

In [236]:
num_entry = 150
count = repair_freq.iat[num_entry]
idx = repair_freq.index[num_entry]
print(f'{idx=}, {count=}')

idx=311, count=12


In [237]:
idx_overview = pd.DataFrame.from_dict(
    id_to_num_objs, 
    orient='index',
    columns=['num_entries', 'num_uni_ids']
).sort_index()
idx_overview.index.name = 'ObID'
idx_overview = idx_overview.sort_values(by='num_entries', ascending=False)
idx_overview

num_entries  num_uni_ids
ObID                          
1110         1289            4
1698          930            2
910           732            2
1726          698            2
1694          646            1
...           ...          ...
2705            1            1
2702            1            1
2701            1            1
2700            1            1
2657            1            1

[1845 rows x 2 columns]

In [190]:
idx_overview.iloc[1500,:]

num_entries    2
num_uni_ids    1
Name: 2472, dtype: int64

- nur ObjektID==0 mehrfach vergeben
- andere IDs nutzbar

In [126]:
anlys_data = data.loc[(data.ObjektID!=0), :].copy()

In [127]:
print(f"{len(data)=}, {len(anlys_data)=}")

len(data)=128936, len(anlys_data)=128419


In [288]:
# VorgangsTypName, VorgangsArtText, VorgangsBeschreibung
prop_interest = [
    'VorgangsTypName', 
    'VorgangsArtText', 
    'VorgangsBeschreibung'
]

prop_interest = [
    'VorgangsArtText', 
    'VorgangsBeschreibung'
]

prop_interest = [
    'VorgangsBeschreibung'
]


In [289]:
# concat features of interest
for it, prop in enumerate(prop_interest):
    if it == 0:
        anlys_data['conc'] = anlys_data[prop].fillna('').astype(str)
    else:
        anlys_data['conc'] = anlys_data['conc'] + ' - ' + anlys_data[prop].fillna('').astype(str)

In [290]:
# test ID with small amount of entries
# e.g. 19
OBJ_ID_INTEREST = 311 # 311 # 87 #19
obj_data = anlys_data.loc[
    ((anlys_data.ObjektID==OBJ_ID_INTEREST) & 
    (anlys_data.VorgangsTypName=='Reparaturauftrag (Portal)')),:
].copy()
"""
obj_data = anlys_data.loc[
    anlys_data.ObjektID==OBJ_ID_INTEREST,:
].copy()
"""

'\nobj_data = anlys_data.loc[\n    anlys_data.ObjektID==OBJ_ID_INTEREST,:\n].copy()\n'

In [291]:
obj_data.head()

VorgangsID  ObjektID                  HObjektText  ObjektArtID  \
254        142283       311  B12 (A), Regalbediengerät,            32   
12485      136107       311  B12 (A), Regalbediengerät,            32   
14160        3998       311  B12 (A), Regalbediengerät,            32   
15016       62522       311  B12 (A), Regalbediengerät,            32   
19343        4122       311  B12 (A), Regalbediengerät,            32   

                                     ObjektArtText  VorgangsTypID  \
254    Flurförderzeuge / Putzmaschine / Rasenmäher              3   
12485  Flurförderzeuge / Putzmaschine / Rasenmäher              3   
14160  Flurförderzeuge / Putzmaschine / Rasenmäher              3   
15016  Flurförderzeuge / Putzmaschine / Rasenmäher              3   
19343  Flurförderzeuge / Putzmaschine / Rasenmäher              3   

                 VorgangsTypName VorgangsDatum  VorgangsStatusId  \
254    Reparaturauftrag (Portal)    2021-11-02                 5   
12485  Reparaturauftrag (Portal)    2021-08-17                 5   
14160  Reparaturauftrag (Portal)    2019-07-12                 5   
15016  Reparaturauftrag (Portal)    2020-10-22                 5   
19343  Reparaturauftrag (Portal)    2019-07-23                 0   

       VorgangsPrioritaet  ... VorgangsOrt VorgangsArtText ErledigungsDatum  \
254                     0  ...        None  Flurförderzeug       2021-11-23   
12485                   0  ...        None  Flurförderzeug       2021-08-23   
14160                   0  ...        None  Flurförderzeug       2019-07-18   
15016                   0  ...        None  Flurförderzeug       2020-10-23   
19343                   0  ...        None  Flurförderzeug       2019-08-27   

            ErledigungsArtText  \
254      Extern - Kundendienst   
12485       Extern - Reparatur   
14160             Kundendienst   
15016  Intern UTT - Reparatur    
19343        Externe Reparatur   

                                 ErledigungsBeschreibung MPMelderArbeitsplatz  \
254    Externer Kundendienst wurde durchgeführt\n\nBe...              Versand   
12485  Externe Reparatur wurde durchgeführt\n\nBeanst...              Versand   
14160                                               None              Versand   
15016  Kettenmitnehmer für Gabeldrehen angefertigt (F...              Versand   
19343               Wurde durch Hr. Heuberger repariert.              Versand   

      MPAbteilungBezeichnung Arbeitsbeginn ErstellungsDatum  \
254                  Versand    2021-11-23       2021-11-02   
12485                Versand    2021-08-23       2021-08-17   
14160                Versand    2019-07-12       2019-07-12   
15016                Versand    2020-10-22       2020-10-22   
19343                Versand    2019-08-27       2019-07-23   

                                                    conc  
254    Regalbediengerät fällt immer wieder aus.\nFehl...  
12485  Hochregalstapler stoppt ständig.\nFehleranzeig...  
14160  Hier wird ein Hochlagerstapler Spezialist benö...  
15016  Gabeldrehen defekt > Kette gerissen\n\nSeitenh...  
19343  Herrn Langner bitte nochmals anfordern. Aktuel...  

[5 rows x 21 columns]

In [292]:
batch = obj_data.conc.to_list()
batch

['Regalbediengerät fällt immer wieder aus.\nFehlercode VZK ER 204/ER 226 während der Fahrt.\nFehlercode VZK ER 208 / ER 209',
 'Hochregalstapler stoppt ständig.\nFehleranzeige: VZA ER 179',
 'Hier wird ein Hochlagerstapler Spezialist benötigt..\n\nToyota Herr Jörg Langner tel_Nr. 0172-8218647 UVV\nDambach B12 (A)\n\n\nFehlermeldung:\nKetten schlaff\nFehlermeldung: VZK - ER229\n\n\nfehlermeldung trift nur sporadisch auf...\nLaut Herr Frick beibt Gerät in Höhe stehen und fährt erst nach mehrmaligem Neustart oder teilweiseerst nach bis zu ca. 30Min.\nwieder. \n\nLaut Herr Spennesberger soll Herr Langner (Toyota) anscheinend nächste Woche auch zur UVV erscheinen.',
 'Gabeldrehen defekt > Kette gerissen\n\nSeitenhub defekt > Führung verbogen gerissen\n\nStapler ist irgendwo (? Regal ? ) angefahren\n\n',
 'Herrn Langner bitte nochmals anfordern. Aktuell steht das Fahrzeug. Fehlercode VZA OK / VZK Error(s) Er229 / VZB OK\nFr. Stöppel hat Herr Langer benachrichtigt.\nElektriker bitte Schalter 

In [293]:
embds = model_stfr.encode(batch)

Batches: 100%|██████████| 1/1 [00:01<00:00,  1.77s/it]


In [294]:
cos_sim = sentence_transformers.util.cos_sim(embds, embds).numpy()
np.fill_diagonal(cos_sim, 0.)
cos_sim = np.triu(cos_sim)
#cos_sim

In [299]:
THRESHOLD = 0.5
#np.where(cos_sim > THRESHOLD, cos_sim, 0)
indices = np.argwhere(cos_sim >= THRESHOLD)

In [287]:
for idx_pair in indices:
    idx1 = idx_pair[0]
    idx2 = idx_pair[1]
    text1 = batch[idx1]
    text2 = batch[idx2]
    
    cos_sim_val = cos_sim[idx1,idx2]
    
    print(f"{text1=}, \n {text2=}, \n {cos_sim_val=} \n\n")

text1='Reparaturauftrag (Portal) - Allgemeine Reparaturarbeiten  - bei Laser1 an Bandsäge band abgerissen\nund bitte Hydraulikbremsfeder kontrollieren', 
 text2='Reparaturauftrag (Portal) - Allgemeine Reparaturarbeiten  - Bandsäge ein-aus schalter defekt.\n(Haltering von Stellschraube gebrochen) dieser fährt auf Endschalter', 
 cos_sim_val=0.60256654 


text1='Reparaturauftrag (Portal) - Allgemeine Reparaturarbeiten  - bei Laser1 an Bandsäge band abgerissen\nund bitte Hydraulikbremsfeder kontrollieren', 
 text2='Reparaturauftrag (Portal) - Allgemeine Reparaturarbeiten  - Bandsäge defekt geht sehr schwer hoch Hydraulik Problem     NICHT ERLEDIGT!!!!!!!\n\n13.06.2022: Feder eingebaut durch Hr. Özdemir und funtkionstüchtig', 
 cos_sim_val=0.56998414 


text1='Reparaturauftrag (Portal) - Allgemeine Reparaturarbeiten  - Bandsäge ein-aus schalter defekt.\n(Haltering von Stellschraube gebrochen) dieser fährt auf Endschalter', 
 text2='Reparaturauftrag (Portal) - Allgemeine Reparaturarbeiten  

In [300]:
for idx_pair in indices:
    idx1 = idx_pair[0]
    idx2 = idx_pair[1]
    text1 = batch[idx1]
    text2 = batch[idx2]
    
    cos_sim_val = cos_sim[idx1,idx2]
    
    print(f"{text1=}, \n {text2=}, \n {cos_sim_val=} \n\n")

text1='Regalbediengerät fällt immer wieder aus.\nFehlercode VZK ER 204/ER 226 während der Fahrt.\nFehlercode VZK ER 208 / ER 209', 
 text2='Hochregalstapler stoppt ständig.\nFehleranzeige: VZA ER 179', 
 cos_sim_val=0.5726533 


text1='Regalbediengerät fällt immer wieder aus.\nFehlercode VZK ER 204/ER 226 während der Fahrt.\nFehlercode VZK ER 208 / ER 209', 
 text2='Herrn Langner bitte nochmals anfordern. Aktuell steht das Fahrzeug. Fehlercode VZA OK / VZK Error(s) Er229 / VZB OK\nFr. Stöppel hat Herr Langer benachrichtigt.\nElektriker bitte Schalter messen evtl. tauschen\nHerr Frick und Herr Hochberger wissen bescheid', 
 cos_sim_val=0.5984524 


text1='Hochregalstapler stoppt ständig.\nFehleranzeige: VZA ER 179', 
 text2='Herrn Langner bitte nochmals anfordern. Aktuell steht das Fahrzeug. Fehlercode VZA OK / VZK Error(s) Er229 / VZB OK\nFr. Stöppel hat Herr Langer benachrichtigt.\nElektriker bitte Schalter messen evtl. tauschen\nHerr Frick und Herr Hochberger wissen bescheid', 
 cos_